# Eff. matching to GEN particle


   * [Efficiency vs $\eta$](#Effinciency-vs-$\eta$)
   * [Efficiency vs $p_{T}$](#Efficiency-vs-$p_{T}$)
   * [Turn-on curves](#Turn-on-curves)


In [1]:
import sys
sys.path.insert(0, '..')
import ROOT
import root_numpy as rnp
import python.l1THistos as histos
import math
import uuid
import pandas as pd

ROOT.enableJSVis()
#ROOT.enableJSVis()

#from drawingTools import *

normalized_histos = list()
    

Welcome to JupyROOT 6.14/02


In [2]:
# %load ../drawingTools
import ROOT
import math
import uuid

# some useful globals, mainly to deal with ROOT idiosyncrasies
c_idx = 0
p_idx = 0
colors = range(1, 6)
stuff = []
f_idx = 0

ROOT.gStyle.SetPadBottomMargin(0.13)
ROOT.gStyle.SetPadLeftMargin(0.13)
ROOT.gStyle.SetPadRightMargin(0.30)

ROOT.gStyle.SetCanvasBorderMode(0)
ROOT.gStyle.SetCanvasColor(0)
ROOT.gStyle.SetCanvasDefH(600)
ROOT.gStyle.SetCanvasDefW(800)

# define some utility functions
def newCanvas(name=None, title=None, xdiv=0, ydiv=0, form=4):
    global c_idx
    if name is None:
        name = 'c_{}'.format(uuid.uuid4().hex[:6])
        c_idx += 1
    if title is None:
        title = name
    # print name, title
    canvas = ROOT.TCanvas(name, title)
    if(xdiv*ydiv != 0):
        canvas.Divide(xdiv, ydiv)
    global stuff
    stuff.append(canvas)
    return canvas


def draw(plot, options='', text=None):
    c = newCanvas()
    c.cd()
    plot.Draw(options)
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw('same')

    c.Draw()

    return


def getLegend(x1=0.7, y1=0.71, x2=0.95, y2=0.85):
    global stuff
    legend = ROOT.TLegend(x1, y1, x2, y2)
    stuff.append(legend)
    legend.SetFillColor(0)
    legend.SetFillStyle(0)
    legend.SetBorderSize(0)
    legend.SetTextSize(0.05)
    return legend


def drawAndProfileX(plot2d, miny=None, maxy=None, do_profile=True, options='', text=None):
    global p_idx
    if miny and maxy:
        plot2d.GetYaxis().SetRangeUser(miny, maxy)
    c = newCanvas()
    c.SetGrid(1, 1)
    c.cd()
    plot2d.Draw(options)
    ROOT.gPad.SetGrid(1, 1)
    ROOT.gStyle.SetGridColor(15)

    if do_profile:
        profname = plot2d.GetName()+'_prof_'+str(p_idx)
        p_idx += 1
        firstbin = 1
        lastbin = -1
        prof = plot2d.ProfileX(profname, firstbin, lastbin, 's')
        prof.SetMarkerColor(2)
        prof.SetLineColor(2)
        prof.Draw('same')

    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw('same')

    c.Draw()


def getText(text, ndc_x, ndc_y):
    global stuff
    rtext = ROOT.TLatex(ndc_x, ndc_y, text)
    stuff.append(rtext)
    rtext.SetNDC(True)
    # rtext.SetTextFont(40)
    rtext.SetTextSize(0.03)
    return rtext


def drawSame(histograms,
             labels,
             options='',
             norm=False,
             logy=False,
             min_y=None,
             max_y=None,
             text=None,
             y_axis_label=None,
             x_axis_label=None,
             v_lines=None,
             h_lines=None):
    global colors
    global stuff
    c = newCanvas(title=histograms[0].GetName())
    c.cd()
    leg = getLegend()

    max_value = max_y
    min_value = min_y
    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in histograms])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in histograms])*1.2

    for hidx, hist in enumerate(histograms):
        hist.SetLineColor(colors[hidx])
        if 'TH' in hist.ClassName():
            hist.SetStats(False)
        if norm:
            hist.DrawNormalized('same'+','+options, 1.)
        else:
            if hidx:
                hist.Draw('same'+','+options)
            else:
                hist.Draw(options)
        leg.AddEntry(histograms[hidx], labels[hidx], 'l')

    histograms[0].GetYaxis().SetRangeUser(min_value, max_value)
    if y_axis_label:
        histograms[0].GetYaxis().SetTitle(y_axis_label)
    if x_axis_label:
            histograms[0].GetXaxis().SetTitle(x_axis_label)

    leg.Draw()
    c.Draw()
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")
    if logy:
        c.SetLogy()

    if v_lines:
        for v_line_x in v_lines:
            aline = ROOT.TLine(v_line_x, c.GetUymin(), v_line_x,  c.GetUymax())
            aline.SetLineStyle(2)
            aline.Draw("same")
            stuff.append(aline)
    if h_lines:
        for h_line_y in h_lines:
            aline = ROOT.TLine(c.GetUxmin(), h_line_y, c.GetUxmax(),  h_line_y)
            aline.SetLineStyle(2)
            aline.Draw("same")
            stuff.append(aline)
    c.Update()


def drawProfileX(histograms, labels, options=''):
    profiles = [hist.ProfileX() for hist in histograms]
    drawSame(profiles, labels, options)


def drawSeveral(histograms, labels, options='', do_profile=False, miny=None, maxy=None, text=None):
    ydiv = int(math.ceil(float(len(histograms))/2))
    for hidx in range(0, len(histograms)):
        newtext = labels[hidx]
        if text:
            newtext = '{}: {}'.format(labels[hidx], text)
        if do_profile:
            drawAndProfileX(histograms[hidx], miny=miny, maxy=maxy, options=options, do_profile=do_profile, text=newtext)
        else:
            draw(histograms[hidx], options=options, text=newtext)


def drawProfileRatio(prof1, prof2, ymin=None, ymax=None, text=None):
    hist1 = prof1.ProjectionX(uuid.uuid4().hex[:6])
    hist2 = prof2.ProjectionX(uuid.uuid4().hex[:6])
    hist1.Divide(hist2)
    draw(hist1)
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")

    if ymin is not None and ymax is not None:
        hist1.GetYaxis().SetRangeUser(ymin, ymax)
    ROOT.gPad.Update()


# mean+-nsigmas*RMS.
def drawGaussFit(histo, nsigmas, min, max):
    minfit = histo.GetMean() - nsigmas*histo.GetRMS()
    maxfit = histo.GetMean() + nsigmas*histo.GetRMS()
    drawGFit(histo, min, max, minfit, maxfit)


# Fit a histogram in the range (minfit, maxfit) with a gaussian and
# draw it in the range (min, max)
def drawGFit(histo, min, max, minfit, maxfit):
    # static int i = 0
    # i++
    # gPad->SetGrid(1,1);
    # gStyle->SetGridColor(15);
    histo.GetXaxis().SetRangeUser(min,max)
    global f_idx
    nameF1 = "g{}".format(f_idx)
    f_idx +=1
    g1 = ROOT.TF1(nameF1,"gaus",minfit,maxfit)
    g1.SetLineColor(2)
    g1.SetLineWidth(2)
    histo.Fit(g1,"R")


def drawGraphsSame(histograms, labels, options='', norm=False, logy=False, min_y=None, max_y=None, text=None):
    global colors
    c = newCanvas()
    c.cd()
    leg = getLegend()

    for hidx in range(0, len(histograms)):
        histograms[hidx].SetLineColor(colors[hidx])
        histograms[hidx].Draw('same'+','+options)
        leg.AddEntry(histograms[hidx], labels[hidx], 'l')

    max_value = max_y
    min_value = min_y
    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in histograms])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in histograms])*1.2
    histograms[0].GetYaxis().SetRangeUser(min_value, max_value)
    leg.Draw()
    c.Draw()
    if logy:
        c.SetLogy()
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")
    c.Update()


In [30]:
def drawSame(histograms,
             labels,
             options='',
             norm=False,
             logy=False,
             min_y=None,
             max_y=None,
             text=None,
             y_axis_label=None,
             x_axis_label=None,
             v_lines=None,
             h_lines=None):
    global colors
    global stuff
    c = newCanvas(title=histograms[0].GetName())
    c.cd()
    leg = getLegend()
    
    max_value = max_y
    min_value = min_y
    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in histograms])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in histograms])*1.2

    for hidx, hist in enumerate(histograms):
        hist.SetLineColor(colors[hidx])
        if 'TH' in hist.ClassName():
            hist.SetStats(False)
        if norm:
            hist.DrawNormalized('same'+','+options, 1.)
        else:
            if hidx:
                hist.Draw('same'+','+options)
            else:
                hist.Draw(options+'PA')
        leg.AddEntry(histograms[hidx], labels[hidx], 'l')

    histograms[0].GetYaxis().SetRangeUser(min_value, max_value)
    if y_axis_label:
        histograms[0].GetYaxis().SetTitle(y_axis_label)
    if x_axis_label:
            histograms[0].GetXaxis().SetTitle(x_axis_label)

    leg.Draw()
    c.Draw()
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")
    if logy:
        c.SetLogy()

    if v_lines:
        for v_line_x in v_lines:
            aline = ROOT.TLine(v_line_x, c.GetUymin(), v_line_x,  c.GetUymax())
            aline.SetLineStyle(2)
            aline.Draw("same")
            stuff.append(aline)
    if h_lines:
        for h_line_y in h_lines:
#             print h_line_y, c.GetUxmin(), c.GetUxmax()
            aline = ROOT.TLine(c.GetUxmin(), h_line_y, c.GetUxmax(),  h_line_y)
            aline.SetLineStyle(2)
            c.cd()
            aline.Draw("same")
            stuff.append(aline)
    c.Update()


In [3]:
# %load samples.py
import ROOT

version = 'v53'

files = {}
file_keys = {}



class RootFile:
    def __init__(self, file_name):
        global file
        self.file_name = file_name
        if self.file_name not in files.keys():
            print 'get file: {}'.format(self.file_name)
            files[self.file_name] = ROOT.TFile(self.file_name)
        self._file = files[self.file_name]
        self._file_keys = None

    def cd(self):
        self._file.cd()

    def GetListOfKeys(self):
        global file_keys
        if self.file_name not in file_keys.keys():
            print 'get list'
            file_keys[self.file_name] = self._file.GetListOfKeys()
        self._file_keys = file_keys[self.file_name]
        return self._file_keys

class Sample():
    def __init__(cls, name, label, version=None):
        cls.name = name
        cls.label = label
        if version:
            version = '_'+version
        else:
            version = ''
        cls.histo_filename = '../plots1/histos_{}{}.root'.format(cls.name, version)
        cls.histo_file = ROOT.TFile(cls.histo_filename, 'r')#RootFile(cls.histo_filename)


# sample_names = ['ele_flat2to100_PU0',
#                 'ele_flat2to100_PU200',
#                 'photonPt35_PU0',
#                 'photonPt35_PU200']


def get_label_dict(selections):
    dictionary = {}
    for sel in selections:
        dictionary[sel.name] = sel.label
    return dictionary



class HProxy:
    def __init__(self, classtype, tp, tp_sel, gen_sel, root_file):
        self.classtype = classtype
        self.tp = tp
        self.tp_sel = tp_sel
        self.gen_sel = gen_sel
        self.root_file = root_file
        self.instance = None


    def get(self):
        if self.instance is None:
            name = '{}_{}_{}'.format(self.tp, self.tp_sel, self.gen_sel)
            if self.gen_sel == None:
                name = '{}_{}'.format(self.tp, self.tp_sel)
            self.instance = self.classtype(name, self.root_file)
        return self.instance

class HPlot:
    def __init__(self, samples, tp_sets, tp_selections, gen_selections):
        self.tp_sets = tp_sets
        self.tp_selections = tp_selections
        self.gen_selections = gen_selections
        self.pus = []
        for sample in samples:
            self.pus.append(sample.label)
        self.data = pd.DataFrame(columns=['sample', 'pu', 'tp', 'tp_sel', 'gen_sel', 'classtype', 'histo'])
        self.labels_dict = {}

        self.labels_dict.update(tp_sets)
        self.labels_dict.update(tp_selections)
        self.labels_dict.update(gen_selections)
        self.labels_dict.update({'PU0': 'PU0', 'PU200': 'PU200'})

    def cache_histo(self,
                    classtype,
                    samples,
                    pus,
                    tps,
                    tp_sels,
                    gen_sels):
        for sample in samples:
            print sample
            for tp in tps:
                for tp_sel in tp_sels:
                    if gen_sels is None:
                        self.data = self.data.append({'sample': 'ele',
                                                        'pu': sample.label,
                                                        'tp': tp,
                                                        'tp_sel': tp_sel,
                                                        'gen_sel': None,
                                                        'classtype': classtype,
                                                        'histo': HProxy(classtype, tp, tp_sel, None, sample.histo_file)}
                                                          , ignore_index=True)
                    else:
                        for gen_sel in gen_sels:
                            print sample, tp, tp_sel, gen_sel
                            self.data = self.data.append({'sample': 'ele',
                                                            'pu': sample.label,
                                                            'tp': tp,
                                                            'tp_sel': tp_sel,
                                                            'gen_sel': gen_sel,
                                                            'classtype': classtype,
                                                            'histo': HProxy(classtype, tp, tp_sel, gen_sel, sample.histo_file)}
                                                              , ignore_index=True)



    def get_histo(self,
                  classtype,
                  sample=None,
                  pu=None,
                  tp=None,
                  tp_sel=None,
                  gen_sel=None):
        histo = None
        labels = []
        text = ''
        query = '(pu == @pu) & (tp == @tp) & (tp_sel == @tp_sel) & (classtype == @classtype)'
        if gen_sel is not None:
            query += '& (gen_sel == @gen_sel)'
        histo_df = self.data.query(query)

        if histo_df.empty:
            print 'No match found for: pu: {}, tp: {}, tp_sel: {}, gen_sel: {}, classtype: {}'.format(pu, tp, tp_sel, gen_sel, classtype)


        field_counts = histo_df.apply(lambda x: len(x.unique()))
        label_fields = []
        text_fields = []
        # print field_counts
        for field in field_counts.iteritems():
            if(field[1] > 1 and field[0] != 'histo' and field[0] != 'sample'):
                label_fields.append(field[0])
            if(field[1] == 1 and field[0] != 'histo' and field[0] != 'classtype' and field[0] != 'sample'):
                if(gen_sel is None and field[0] == 'gen_sel'):
                    continue
                text_fields.append(field[0])

#         print 'label fields: {}'.format(label_fields)
#         print 'text fields: {}'.format(text_fields)

        for item in histo_df[label_fields].iterrows():
            labels.append(', '.join([self.labels_dict[tx] for tx in item[1].values if self.labels_dict[tx] != '']))

        #print labels
        text = ', '.join([self.labels_dict[fl] for fl in histo_df[text_fields].iloc[0].values if self.labels_dict[fl] != ''])
        histo = [his.get() for his in  histo_df['histo'].values]
        return histo, labels, text



# -------------------------------------------------------------------------
sample_ele_flat2to100_PU0 = Sample('ele_flat2to100_PU0', 'PU0', version)
sample_ele_flat2to100_PU200 = Sample('ele_flat2to100_PU200', 'PU200', version)

samples_ele = [sample_ele_flat2to100_PU0, sample_ele_flat2to100_PU200]

# -------------------------------------------------------------------------

sample_photon_flat8to150_PU0 = Sample('photon_flat8to150_PU0', 'PU0', version)
sample_photon_flat8to150_PU200 = Sample('photon_flat8to150_PU200', 'PU0', version)

samples_photons = [sample_photon_flat8to150_PU0, sample_photon_flat8to150_PU200]


sample_gPt35_PU0 = Sample('photonPt35_PU0', 'Pt35 PU0', version)
sample_gPt35_PU200 = Sample('photonPt35_PU200', 'Pt35 PU200', version)

sample_hadronGun_PU0 = Sample('hadronGun_PU0', 'PU0', version)
sample_hadronGun_PU200 = Sample('hadronGun_PU200', 'PU200', version)


samples_photon = [sample_gPt35_PU0, sample_gPt35_PU200]
samples_hadrons = [sample_hadronGun_PU0, sample_hadronGun_PU200]

sample_nugunrate = Sample('nugun_alleta_pu200', 'PU200', version)
samples_nugunrates = [sample_nugunrate]


from python.selections import tp_rate_selections
from python.selections import tp_match_selections
from python.selections import gen_part_selections

tpsets = {'DEF': 'NNDR',
          'DEFCalib': 'NNDR Calib v1'}

tpset_selections = {}

gen_selections = {}
samples = []


#tpset_selections.update(get_label_dict(tp_rate_selections))
tpset_selections.update(get_label_dict(tp_match_selections))

gen_selections.update(get_label_dict(gen_part_selections))


gen_part_selections: 15


Error in <TFile::TFile>: file ../plots1/histos_photonPt35_PU0_v53.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_photonPt35_PU200_v53.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_hadronGun_PU0_v53.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_hadronGun_PU200_v53.root does not exist


In [4]:
%%time
# for key in samples_ele[0].histo_file.GetListOfKeys():
#     #pass
#     key.GetName()
# print len(samples_ele[0].histo_file.GetListOfKeys())
# l = [histo for histo in samples_ele[0].histo_file.GetListOfKeys()]
l = [(histo.ReadObj(), histo.GetName()) for histo in samples_ele[0].histo_file.GetListOfKeys() if 'DEF_all'+'_' in histo.GetName()]

CPU times: user 13 ms, sys: 1.45 ms, total: 14.5 ms
Wall time: 36.4 ms


In [5]:
%%time

hplot = HPlot(samples, tpsets, tpset_selections, gen_selections)
samples = samples_ele


hplot.cache_histo(classtype=histos.HistoSetEff, 
                  samples=samples,
                  pus=[],
                  tps=tpsets,
                  tp_sels=tpset_selections,
                  gen_sels=gen_selections)



<__main__.Sample instance at 0x11fbe5950>
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaB
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaABC
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaA
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENPt40
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaC
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaAB
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaE
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaD
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaBC
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENPt30
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENPt20
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaBCD
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENPt10
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GENEtaBCDE
<__main__.Sample instance at 0x11fbe5950> DEFCalib Em GEN
<__main__.Sample instan

<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENEtaE
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENEtaD
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENEtaBC
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENPt30
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENPt20
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENEtaBCD
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENPt10
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GENEtaBCDE
<__main__.Sample instance at 0x11fbe5950> DEFCalib Pt25 GEN
<__main__.Sample instance at 0x11fbe5950> DEFCalib Emv1Pt25 GENEtaB
<__main__.Sample instance at 0x11fbe5950> DEFCalib Emv1Pt25 GENEtaABC
<__main__.Sample instance at 0x11fbe5950> DEFCalib Emv1Pt25 GENEtaA
<__main__.Sample instance at 0x11fbe5950> DEFCalib Emv1Pt25 GENPt40
<__main__.Sample instance at 0x11fbe5950> DEFCalib Emv1Pt25 GENEtaC
<__main__.Sample instance at 0x11fbe5950> DEFCalib Emv1Pt25 GENEtaAB
<__main__.S

<__main__.Sample instance at 0x11fbe5950> DEF Pt10 GENPt10
<__main__.Sample instance at 0x11fbe5950> DEF Pt10 GENEtaBCDE
<__main__.Sample instance at 0x11fbe5950> DEF Pt10 GEN
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaB
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaABC
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaA
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENPt40
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaC
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaAB
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaE
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaD
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaBC
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENPt30
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENPt20
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENEtaBCD
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt30 GENPt10

<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaA
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENPt40
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaC
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaAB
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaE
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaD
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaBC
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENPt30
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENPt20
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaBCD
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENPt10
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GENEtaBCDE
<__main__.Sample instance at 0x11fbe5950> DEF EmPt25 GEN
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt10 GENEtaB
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt10 GENEtaABC
<__main__.Sample instance at 0x11fbe5950> DEF Emv1Pt10 GENEtaA
<__main__.Sam

<__main__.Sample instance at 0x11fbe5710> DEFCalib Emv1Pt20 GENPt30
<__main__.Sample instance at 0x11fbe5710> DEFCalib Emv1Pt20 GENPt20
<__main__.Sample instance at 0x11fbe5710> DEFCalib Emv1Pt20 GENEtaBCD
<__main__.Sample instance at 0x11fbe5710> DEFCalib Emv1Pt20 GENPt10
<__main__.Sample instance at 0x11fbe5710> DEFCalib Emv1Pt20 GENEtaBCDE
<__main__.Sample instance at 0x11fbe5710> DEFCalib Emv1Pt20 GEN
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaB
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaABC
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaA
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENPt40
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaC
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaAB
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaE
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaD
<__main__.Sample instance at 0x11fbe5710> DEFCalib Pt30 GENEtaBC
<__main__.S

<__main__.Sample instance at 0x11fbe5710> DEF Em GENEtaE
<__main__.Sample instance at 0x11fbe5710> DEF Em GENEtaD
<__main__.Sample instance at 0x11fbe5710> DEF Em GENEtaBC
<__main__.Sample instance at 0x11fbe5710> DEF Em GENPt30
<__main__.Sample instance at 0x11fbe5710> DEF Em GENPt20
<__main__.Sample instance at 0x11fbe5710> DEF Em GENEtaBCD
<__main__.Sample instance at 0x11fbe5710> DEF Em GENPt10
<__main__.Sample instance at 0x11fbe5710> DEF Em GENEtaBCDE
<__main__.Sample instance at 0x11fbe5710> DEF Em GEN
<__main__.Sample instance at 0x11fbe5710> DEF all GENEtaB
<__main__.Sample instance at 0x11fbe5710> DEF all GENEtaABC
<__main__.Sample instance at 0x11fbe5710> DEF all GENEtaA
<__main__.Sample instance at 0x11fbe5710> DEF all GENPt40
<__main__.Sample instance at 0x11fbe5710> DEF all GENEtaC
<__main__.Sample instance at 0x11fbe5710> DEF all GENEtaAB
<__main__.Sample instance at 0x11fbe5710> DEF all GENEtaE
<__main__.Sample instance at 0x11fbe5710> DEF all GENEtaD
<__main__.Sample i

<__main__.Sample instance at 0x11fbe5710> DEF Emv1Pt25 GENEtaBCDE
<__main__.Sample instance at 0x11fbe5710> DEF Emv1Pt25 GEN
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaB
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaABC
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaA
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENPt40
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaC
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaAB
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaE
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaD
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaBC
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENPt30
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENPt20
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaBCD
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENPt10
<__main__.Sample instance at 0x11fbe5710> DEF Pt20 GENEtaBCDE
<__main__.Sample instance at 0x11fbe5710

In [6]:
%%time

for pu in ['PU0', 'PU200']:
    for tp in tpsets:
        for tp_sel in tpset_selections:
            tp_sel_den = 'all'
            if 'Pt' in tp_sel:
                # print tp_sel
                tp_sel_den = tp_sel.split('Pt')[0]
                if tp_sel_den == '':
                    tp_sel_den = 'all'
                print '{} den -> {}'.format(tp_sel, tp_sel_den) 
            else:
                continue
            for gen_sel in ['GEN', 'GENEtaA', 'GENEtaAB', 'GENEtaABC', 'GENEtaB', 'GENEtaBC', 'GENEtaBCD', 'GENEtaBCDE', 'GENEtaC', 'GENEtaD', 'GENEtaE']:
                hsetden = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel_den, gen_sel)
                hset = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, gen_sel)
#                 print hset[0][0].name
#                 print hsetden[0][0].name
                hset[0][0].computeTurnOn(hsetden[0][0].h_num)


Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt25 den -> all
Emv1Pt25 den -> Emv1
Pt20 den -> all
EmPt10 den -> Em
EmPt25 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt25 den -> all
Emv1Pt25 den -> Emv1
Pt20 den -> all
EmPt10 den -> Em
EmPt25 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt25 den -> all
Emv1Pt25 den -> Emv1
Pt20 den -> all
EmPt10 den -> Em
EmPt25 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt25 den -> all
Emv1Pt25 den -> Emv1
Pt20 den -> all
EmPt10 den -> Em
EmPt25 den -> Em
Emv1Pt10 den -> Emv1
CPU times: user 1min, sys: 7.58 s, total: 1min 7s
Wall time: 1min 9s


In [7]:
hplot.data

sample     pu        tp    tp_sel     gen_sel  \
0      ele    PU0  DEFCalib        Em     GENEtaB   
1      ele    PU0  DEFCalib        Em   GENEtaABC   
2      ele    PU0  DEFCalib        Em     GENEtaA   
3      ele    PU0  DEFCalib        Em     GENPt40   
4      ele    PU0  DEFCalib        Em     GENEtaC   
5      ele    PU0  DEFCalib        Em    GENEtaAB   
6      ele    PU0  DEFCalib        Em     GENEtaE   
7      ele    PU0  DEFCalib        Em     GENEtaD   
8      ele    PU0  DEFCalib        Em    GENEtaBC   
9      ele    PU0  DEFCalib        Em     GENPt30   
10     ele    PU0  DEFCalib        Em     GENPt20   
11     ele    PU0  DEFCalib        Em   GENEtaBCD   
12     ele    PU0  DEFCalib        Em     GENPt10   
13     ele    PU0  DEFCalib        Em  GENEtaBCDE   
14     ele    PU0  DEFCalib        Em         GEN   
15     ele    PU0  DEFCalib       all     GENEtaB   
16     ele    PU0  DEFCalib       all   GENEtaABC   
17     ele    PU0  DEFCalib       all     GENEtaA   
18     ele    PU0  DEFCalib       all     GENPt40   
19     ele    PU0  DEFCalib       all     GENEtaC   
20     ele    PU0  DEFCalib       all    GENEtaAB   
21     ele    PU0  DEFCalib       all     GENEtaE   
22     ele    PU0  DEFCalib       all     GENEtaD   
23     ele    PU0  DEFCalib       all    GENEtaBC   
24     ele    PU0  DEFCalib       all     GENPt30   
25     ele    PU0  DEFCalib       all     GENPt20   
26     ele    PU0  DEFCalib       all   GENEtaBCD   
27     ele    PU0  DEFCalib       all     GENPt10   
28     ele    PU0  DEFCalib       all  GENEtaBCDE   
29     ele    PU0  DEFCalib       all         GEN   
..     ...    ...       ...       ...         ...   
870    ele  PU200       DEF  Emv1Pt10     GENEtaB   
871    ele  PU200       DEF  Emv1Pt10   GENEtaABC   
872    ele  PU200       DEF  Emv1Pt10     GENEtaA   
873    ele  PU200       DEF  Emv1Pt10     GENPt40   
874    ele  PU200       DEF  Emv1Pt10     GENEtaC   
875    ele  PU200       DEF  Emv1Pt10    GENEtaAB   
876    ele  PU200       DEF  Emv1Pt10     GENEtaE   
877    ele  PU200       DEF  Emv1Pt10     GENEtaD   
878    ele  PU200       DEF  Emv1Pt10    GENEtaBC   
879    ele  PU200       DEF  Emv1Pt10     GENPt30   
880    ele  PU200       DEF  Emv1Pt10     GENPt20   
881    ele  PU200       DEF  Emv1Pt10   GENEtaBCD   
882    ele  PU200       DEF  Emv1Pt10     GENPt10   
883    ele  PU200       DEF  Emv1Pt10  GENEtaBCDE   
884    ele  PU200       DEF  Emv1Pt10         GEN   
885    ele  PU200       DEF      Emv1     GENEtaB   
886    ele  PU200       DEF      Emv1   GENEtaABC   
887    ele  PU200       DEF      Emv1     GENEtaA   
888    ele  PU200       DEF      Emv1     GENPt40   
889    ele  PU200       DEF      Emv1     GENEtaC   
890    ele  PU200       DEF      Emv1    GENEtaAB   
891    ele  PU200       DEF      Emv1     GENEtaE   
892    ele  PU200       DEF      Emv1     GENEtaD   
893    ele  PU200       DEF      Emv1    GENEtaBC   
894    ele  PU200       DEF      Emv1     GENPt30   
895    ele  PU200       DEF      Emv1     GENPt20   
896    ele  PU200       DEF      Emv1   GENEtaBCD   
897    ele  PU200       DEF      Emv1     GENPt10   
898    ele  PU200       DEF      Emv1  GENEtaBCDE   
899    ele  PU200       DEF      Emv1         GEN   

                        classtype                                      histo  
0    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11fbac7e8>  
1    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11fbacdd0>  
2    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11f187fc8>  
3    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11fbc9830>  
4    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11f13fd40>  
5    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11fbac7a0>  
6    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11f1a2128>  
7    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x11f1a2e18>  
8    p

In [8]:
tps = ['DEF', 'DEFCalib']
tp_select = ['all', 'Em' ,'Emv1']
gen_select = ['GEN', 'GENEtaA', 'GENEtaB', 'GENEtaC', 'GENEtaD', 'GENEtaE',
              'GENEtaAB', 'GENEtaABC', 'GENEtaBC', 'GENEtaBCD', 'GENEtaBCDE' ]


## Effinciency vs $\eta$

In [9]:
line_m1p52 = ROOT.TLine(-1.52,0, -1.52, 1.1)
line_m1p52.SetLineStyle(2)
line_p1p52 = ROOT.TLine(1.52,0, 1.52, 1.1)
line_p1p52.SetLineStyle(2)
line_m1p7 = ROOT.TLine(-1.7,0, -1.7, 1.1)
line_m1p7.SetLineStyle(2)
line_p1p7 = ROOT.TLine(1.7,0, 1.7, 1.1)
line_p1p7.SetLineStyle(2)
line_m2p8 = ROOT.TLine(-2.8,0, -2.8, 1.1)
line_m2p8.SetLineStyle(2)
line_p2p8 = ROOT.TLine(2.8,0, 2.8, 1.1)
line_p2p8.SetLineStyle(2)

In [10]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8])
#             print [his.h_num.h_eta.GetName() for his in hsets]

In [11]:
for tp in tps:
    for tp_sel in ['EmPt20', 'Emv1Pt20']:
        for gen_sel in ['GENPt30']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, 
                     text=text, min_y=0, max_y=1.1, 
                     v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8],
                     y_axis_label='(L1>thr. & matched to GEN)/GEN',
                     options='P')
     

In [12]:
for pu in ['PU0', 'PU200']:
    for tp_sel in ['EmPt20', 'Emv1Pt20']:
        for gen_sel in ['GENPt30']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFCalib'], tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8])
   

#### Old vs New EGID: eff vs $\eta$

In [13]:
for pu in ['PU0', 'PU200']:
    for gen_sel in ['GENPt30']:
        hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF'], ['EmPt20', 'Emv1Pt20'], gen_sel)
        # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
        drawSame([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8])
   

## Efficiency vs $p_{T}$

In [14]:
line_y1p0 = ROOT.TLine(0.,1., 110., 1.)
line_y0p95 = ROOT.TLine(0.,0.95, 110., 0.95)
line_y0p95.SetLineStyle(2)

In [16]:
for tp in tps:
    for tp_sel in ['all', 'Em', 'Emv1']:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_eff.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN/GEN', h_lines=[0.95, 1] )


#### OLD VS NEW EGID VS $p_{T}$

In [17]:
for pu in ['PU0', 'PU200']:
    for tp in ['DEF']:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, ['all', 'Em', 'Emv1'], gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_eff.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN/GEN', h_lines=[0.95, 1])


## Turn-on curves

In [18]:
for tp in tps:
    for tp_sel in ['Pt20', 'EmPt20', 'Emv1Pt20', 'Pt30', 'EmPt30', 'Emv1Pt30']:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

In [19]:
for pu in ['PU0', 'PU200']:
    for tp in tps:
        for tp_sel in ['Pt20', 'EmPt20', 'Emv1Pt20', 'Pt30', 'EmPt30', 'Emv1Pt30']:
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, ['GENEtaABC', 'GENEtaBC'])
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

In [20]:
for pu in ['PU0', 'PU200']:
        for tp_sel in ['EmPt20', 'Emv1Pt20', 'EmPt30', 'Emv1Pt30']:
            for gen_sel in gen_select:
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFCalib'], tp_sel, gen_sel)
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

In [21]:
for pu in ['PU0', 'PU200']:
        for tp_sel in ['EmPt20', 'Emv1Pt20', 'EmPt30', 'Emv1Pt30']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFCalib'], tp_sel, ['GENEtaABC', 'GENEtaBC'])
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

## Scaling

In [22]:
def f_yc(x, par):
    return (ROOT.Math.normal_cdf(par[0]*(x[0]-par[1]), par[0]*par[2], 0) - ROOT.TMath.Exp(-par[0]*(x[0]-par[1])+par[0]*par[0]*par[2]*par[2]/2)*ROOT.Math.normal_cdf(par[0]*(x[0]-par[1]), par[0]*par[2], par[0]*par[0]*par[2]*par[2])) * (par[3] - par[4]) + par[4]

tf_yc = ROOT.TF1('tf_yc', f_yc, 0, 100, 5)
tf_yc.SetParameters(1, 20, 4, 1.0, 0.0);
tf_yc.SetParNames("#lambda", "#mu", "#sigma", "Plateau", "Baseline");
tf_yc.SetLineColor(6)
tf_yc.FixParameter(4,0)

tf_yc.SetParLimits(3, 0.8, 1)
tf_yc.SetParLimits(0, 0, 1)

c = newCanvas()
tf_yc.Draw()
c.Draw()


In [23]:

import numpy as np
from array import array

def f_cb(x, par):
    return ROOT.Math.crystalball_function(x[0], par[0], par[1], par[2], par[3])

tf_cb = ROOT.TF1('cb', f_cb, 0, 100, 4)
tf_cb.SetParameters(10., 4., 3, 20.)

def f_cbi(x, par):
    return ROOT.Math.crystalball_cdf(x[0], par[0], par[1], par[2], par[3])
#     tf_cb.SetParameters(par[0], par[1], par[2], par[3])
#     npts = 1000
#     x_ = []
#     w_ = []
   
#     return tf_cb.IntegralFast(npts, np.array(npts), np.array(npts), 0., x[0])
    #return tf_cb.Integral(0., x[0])
    
    
tf_cbi = ROOT.TF1('cbi', f_cbi, 0, 100, 4)
tf_cbi.SetParameters(10., 4., 3, 20.)
tf_cbi.SetLineColor(4)

c = newCanvas()
tf_cbi.Draw()
c.Draw()


    # ROOT::Math::crystalball_function (double x, double alpha, double n, double sigma, double x0=0)

# fitf_cb = ROOT.TF1('cbfunc', 'ROOT.TMath.crystalball_function (x, [0], [1], [2], [3])', 0, 100)
# 

# fitf_cb.SetParameters(1, 1, 1, 0)


In [24]:
# Double_t turnon_func(Double_t *x, Double_t *par)
# {
#   double halfpoint = par[0];
#   double slope = par[1];
#   double plateau = par[2];

#   //double offset = par[3];
#   //double plateau = 1.0;
#   double offset = 0;

#   double pt = TMath::Max(x[0],0.000001);

#    double arg = 0;
#    //cout << pt <<", "<< halfpoint <<", " << slope <<endl;
#    arg = (pt - halfpoint)/(TMath::Sqrt(pt)*slope);
#    double fitval = offset+0.5*plateau*(1+TMath::Erf(arg));
#    return fitval;
# }




def turnon_func1(x, par):

    return 0.5 * par[0] * (1+ROOT.TMath.Erf((x[0]-par[1])/(par[2]*ROOT.TMath.Sqrt(2))))




def turnon_func(x, par):
  
    halfpoint = par[0]
    slope = par[1]
    plateau = par[2]
    offset = 0
    pt = ROOT.TMath.Max(x[0],0.000001)
    arg = 0
    arg = (pt - halfpoint)/(ROOT.TMath.Sqrt(pt)*slope)
    fitval = offset+0.5*plateau*(1+ROOT.TMath.Erf(arg))
    return fitval

fitf_to = ROOT.TF1('myfunc', turnon_func1, 0, 100, 3)
#fitf.SetParNames('#epsilon', "#mu", '#sigma')
fitf_to.SetParameters(1,25,2)
fitf_to.SetLineColor(3)

def fermi(x, params):
    return params[3]*(params[0] - 1/(ROOT.TMath.Exp((x[0]-params[1])/(params[2]))+1))
  
fitf = ROOT.TF1('myfunc', fermi, 0, 100, 4)
fitf.SetParNames('#epsilon', "#mu", '#sigma')
fitf.SetParameters(1,25,2,1)



c = newCanvas()
fitf.Draw()
c.Draw()


In [25]:
ROOT.TVirtualFitter.SetDefaultFitter("Fumili2")
ROOT.TVirtualFitter.SetPrecision(1e-04)

points = []


for pu in ['PU0', 'PU200']:
    for tp in ['DEF', 'DEFCalib']:
        for pt in [10, 20, 25, 30]:
                tp_sel = 'EmPt{}'.format(pt)
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, 'GENEtaBC')
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                h_eff_vs_pt = [his.h_ton.h_pt.CreateGraph() for his in hsets]
                tf_yc.SetParameters(1, 20, 4, 1.0, 0.0);
                result = h_eff_vs_pt[0].Fit(tf_yc, 'MQRS+')
                print '------- {}'.format( text)
                print result.Print()
                pt095 = tf_yc.GetX(0.95)
                points.append((tp, pu, pt, pt095))
                drawSame(h_eff_vs_pt, labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
                ROOT.gStyle.SetOptFit(11111)

------- PU0, NNDR, EGId, p_{T}^{L1}>=10GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=20GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=25GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=30GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=10GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=20GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=25GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=30GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=10GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=20GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=25GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=30GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR Calib v1, EGId, p_{T}^{L

In [26]:
# print points

points_calib_pu0 = [point for point in points if ('Calib' in point[0] and 'PU0' in point[1])]
points_calib_pu200 = [point for point in points if ( 'Calib' in point[0] and 'PU200' in point[1])]

points_nocalib_pu0 = [point for point in points if ('Calib' not in point[0] and 'PU0' in point[1])]
points_nocalib_pu200 = [point for point in points if ( 'Calib' not in point[0] and 'PU200' in point[1])]

# print points
# print points_calib_pu0
# print points_calib_pu200
# print points_nocalib_pu0
# print points_nocalib_pu200

graph_nocalib_pu0 = ROOT.TGraph(len(points_nocalib_pu0), array('d', [point[2] for point in points_nocalib_pu0]), array('d',[point[3] for point in points_nocalib_pu0]))
drawGraphsSame([graph_nocalib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='no calib')
graph_nocalib_pu0.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

graph_calib_pu0 = ROOT.TGraph(len(points_calib_pu0), array('d', [point[2] for point in points_calib_pu0]), array('d',[point[3] for point in points_calib_pu0]))
drawGraphsSame([graph_calib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='calib')
graph_calib_pu0.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)


graph_nocalib_pu200 = ROOT.TGraph(len(points_nocalib_pu200), array('d', [point[2] for point in points_nocalib_pu200]), array('d',[point[3] for point in points_nocalib_pu200]))
drawGraphsSame([graph_nocalib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='no calib')
graph_nocalib_pu200.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

graph_calib_pu200 = ROOT.TGraph(len(points_calib_pu200), array('d', [point[2] for point in points_calib_pu200]), array('d',[point[3] for point in points_calib_pu200]))
drawGraphsSame([graph_calib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='calib')
graph_calib_pu200.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)


****************************************
Minimizer is Linear
Chi2                      =     0.918145
NDf                       =            2
p0                        =      9.09581   +/-   1.03074     
p1                        =      1.25977   +/-   0.0458107   

****************************************
Minimizer is Linear
Chi2                      =      1.88484
NDf                       =            2
p0                        =      6.46857   +/-   1.47683     
p1                        =       1.2917   +/-   0.065637    

****************************************
Minimizer is Linear
Chi2                      =     0.714251
NDf                       =            2
p0                        =      8.86503   +/-   0.909115    
p1                        =      1.26425   +/-   0.0404051   

****************************************
Minimizer is Linear
Chi2                      =      1.38809
NDf                       =            2
p0                        =      6.04031   +/-   1.2

In [27]:
points = []


for pu in ['PU0', 'PU200']:
    for tp in ['DEF', 'DEFCalib']:
        for pt in [10, 20, 25, 30]:
                tp_sel = 'EmPt{}'.format(pt)
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, 'GENEtaABC')
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                h_eff_vs_pt = [his.h_ton.h_pt.CreateGraph() for his in hsets]
                tf_yc.SetParameters(1, 20, 4, 1.0, 0.0);
                result = h_eff_vs_pt[0].Fit(tf_yc, 'MQRS+')
                print '------- {}'.format( text)
                print result.Print()
                pt095 = tf_yc.GetX(0.95)
                points.append((tp, pu, pt, pt095))
                drawSame(h_eff_vs_pt, labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
                ROOT.gStyle.SetOptFit(11111)

------- PU0, NNDR, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=20GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=25GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=30GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=20GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=25GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=30GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=20GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=25GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=30GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR Calib v1, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR Calib v1, EGId, p_{T}^{L1}>=

In [28]:
points_calib_pu0 = [point for point in points if ('Calib' in point[0] and 'PU0' in point[1])]
points_calib_pu200 = [point for point in points if ( 'Calib' in point[0] and 'PU200' in point[1])]

points_nocalib_pu0 = [point for point in points if ('Calib' not in point[0] and 'PU0' in point[1])]
points_nocalib_pu200 = [point for point in points if ( 'Calib' not in point[0] and 'PU200' in point[1])]

print points
# print points_calib_pu0
# print points_calib_pu200
# print points_nocalib_pu0
# print points_nocalib_pu200

graph_nocalib_pu0 = ROOT.TGraph(len(points_nocalib_pu0), array('d', [point[2] for point in points_nocalib_pu0]), array('d',[point[3] for point in points_nocalib_pu0]))
drawGraphsSame([graph_nocalib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='no calib')
graph_nocalib_pu0.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

graph_calib_pu0 = ROOT.TGraph(len(points_calib_pu0), array('d', [point[2] for point in points_calib_pu0]), array('d',[point[3] for point in points_calib_pu0]))
drawGraphsSame([graph_calib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='calib')
graph_calib_pu0.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)


graph_nocalib_pu200 = ROOT.TGraph(len(points_nocalib_pu200), array('d', [point[2] for point in points_nocalib_pu200]), array('d',[point[3] for point in points_nocalib_pu200]))
drawGraphsSame([graph_nocalib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='no calib')
graph_nocalib_pu200.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

graph_calib_pu200 = ROOT.TGraph(len(points_calib_pu200), array('d', [point[2] for point in points_calib_pu200]), array('d',[point[3] for point in points_calib_pu200]))
drawGraphsSame([graph_calib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='calib')
graph_calib_pu200.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

[('DEF', 'PU0', 10, 22.3534494344717), ('DEF', 'PU0', 20, 36.783019374488724), ('DEF', 'PU0', 25, 43.10413863859281), ('DEF', 'PU0', 30, 49.06314741463852), ('DEFCalib', 'PU0', 10, 19.99474332507898), ('DEFCalib', 'PU0', 20, 35.032866502257924), ('DEFCalib', 'PU0', 25, 41.588832113720144), ('DEFCalib', 'PU0', 30, 47.269526958522974), ('DEF', 'PU200', 10, 23.32041951835891), ('DEF', 'PU200', 20, 37.892364844376395), ('DEF', 'PU200', 25, 44.483653708017854), ('DEF', 'PU200', 30, 50.380391686270876), ('DEFCalib', 'PU200', 10, 20.887989501408413), ('DEFCalib', 'PU200', 20, 36.22727094680916), ('DEFCalib', 'PU200', 25, 42.88157597889916), ('DEFCalib', 'PU200', 30, 48.982961197277426)]

****************************************
Minimizer is Linear
Chi2                      =     0.858972
NDf                       =            2
p0                        =      9.31568   +/-   0.996972    
p1                        =      1.34166   +/-   0.0443099   

****************************************
M

In [29]:

samples = samples_ele
tp_sets = ['DEF', 'DEF_em', 'DEF_pt20', 'DEF_pt20_em', 'DEF_pt25', 'DEF_pt25_em', 'DEF_pt30', 'DEF_pt30_em']
particles = ['ele', 'eleA', 'eleB', 'eleC', 'eleD', 'eleAAA', 'eleAA', 'eleBB', 'eleCC', 'eleDD']


labels = [sample.label for sample in samples]




histo_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_num_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_den_df = pd.DataFrame(index=tp_sets, columns=particles)
titles_df = pd.DataFrame(index=tp_sets, columns=particles)
# print histo_num_df
for tp_set in tp_sets:
    for particle in particles:
        histo_df.loc[tp_set][particle] =  [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_eff for sample in samples]
        histo_num_df.loc[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_num for sample in samples]
        histo_den_df.loc[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_den for sample in samples]

        titles_df.loc[tp_set, particle] = '{}, {}'.format(tpset_labels[tp_set], particle_labels[particle])

histo_df



NameError: name 'tpset_labels' is not defined

In [ ]:
titles_df

In [ ]:
dir(histo_df.ele['DEF'][0])


In [ ]:
histo_df.loc['DEF', 'ele']

In [ ]:

for particle in ['ele']:
    for tp_set in tp_sets:
        h_eff_vs_eta = [histo.h_eta.CreateGraph() for histo in histo_df.ele[tp_set]]
        drawGraphsSame(h_eff_vs_eta, labels, text=titles_df.loc[tp_set, particle])



In [ ]:
line095 = ROOT.TLine(0,0.95,110,0.95)
line095.SetLineStyle(2)
for particle in particles:
    for tp_set in tp_sets:
        #print 'particle: {}, TP set: {}, text: {}'.format(particle, tp_set, titles_df.loc[tp_set, particle])
        h_eff_vs_pt = [histo.h_pt.CreateGraph() for histo in histo_df.loc[tp_set, particle]]
        drawGraphsSame(h_eff_vs_pt, labels, text=titles_df.loc[tp_set, particle], min_y=0., max_y=1.1)
        line095.Draw('same')

In [ ]:
histo_den_df

In [ ]:
# build turnon

for particle in particles:
    TP_set_den = 'DEF' # -> L1 matched/GEN
    TP_set_num_l = ['DEF_pt20', 'DEF_pt25', 'DEF_pt30'] # -> L1 matched & above threshols / GEN
    
    histo_den = [histo for histo in histo_num_df.loc[TP_set_den][particle]] # -> L1 matched
    for TP_set_num in TP_set_num_l:
        histo_num = [histo for histo in histo_num_df.loc[TP_set_num][particle]] # -> L1 matched & above threshols

        histos_turnon = []
        for idx,histo_num in enumerate(histo_num):
            histo_turnon_num = histo_num.h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_num)
            histo_turnon_den = histo_den[idx].h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_den)
            hton = ROOT.TEfficiency(histo_turnon_num, histo_turnon_den)
            stuff.append(hton)
            histos_turnon.append(hton)
        drawGraphsSame(histos_turnon, labels, text=titles_df.loc[TP_set_num, particle])

In [ ]:
for particle in particles:
    TP_set_den = 'DEF_em' # -> L1 matched/GEN
    TP_set_num_l = ['DEF_pt20_em', 'DEF_pt25_em', 'DEF_pt30_em'] # -> L1 matched & above threshols / GEN
    
    histo_den = [histo for histo in histo_num_df.loc[TP_set_den][particle]] # -> L1 matched
    for TP_set_num in TP_set_num_l:
        histo_num = [histo for histo in histo_num_df.loc[TP_set_num][particle]] # -> L1 matched & above threshols

        histos_turnon = []
        for idx,histo_num in enumerate(histo_num):
            histo_turnon_num = histo_num.h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_num)
            histo_turnon_den = histo_den[idx].h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_den)
            hton = ROOT.TEfficiency(histo_turnon_num, histo_turnon_den)
            stuff.append(hton)
            histos_turnon.append(hton)
        drawGraphsSame(histos_turnon, labels, text=titles_df.loc[TP_set_num, particle])

# Photon pt35 GeV 1.6 < |eta| < 2.8 

In [ ]:

samples = samples_photon
tp_sets = ['DEF', 'DEF_em']
particles = ['photon']
labels = [sample.label for sample in samples]

histo_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_num_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_den_df = pd.DataFrame(index=tp_sets, columns=particles)

for tp_set in tp_sets:
    for particle in particles:
        histo_df.loc[tp_set][particle] =  [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_eff for sample in samples]
        histo_num_df[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_num for sample in samples]
        histo_den_df[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_den for sample in samples]

        histo_df



In [ ]:
dir(histo_df.photon['DEF'][0])


In [ ]:
tp_set = 'DEF'
h_eff_vs_eta = [histo.h_eta.CreateGraph() for histo in histo_df.photon[tp_set]]
drawGraphsSame(h_eff_vs_eta, labels)

tp_set = 'DEF_em'
h_eff_vs_eta = [histo.h_eta.CreateGraph() for histo in histo_df.photon[tp_set]]
drawGraphsSame(h_eff_vs_eta, labels)
